# Objectives {.unnumbered}

By the end of this lab, you will:
1. Load and analyze the **Lightcast dataset** in **Spark DataFrame**.
2. Create **five easy and three medium-complexity visualizations** using **Plotly**.
3. Explore **salary distributions, employment trends, and job postings**.
4. Analyze **skills in relation to NAICS/SOC/ONET codes and salaries**.
5. Customize **colors, fonts, and styles** in all visualizations (**default themes result in a 2.5-point deduction**).
6. Follow **best practices for reporting on data communication**.

# Step 1: Load the Dataset {.unnumbered}


In [8]:
import pandas as pd
import plotly.express as px
import plotly.io as pio
pio.renderers.default = "vscode"
from pyspark.sql import SparkSession
from pyspark.sql.functions import col


# Initialize Spark Session
spark = SparkSession.builder.appName("LightcastData").getOrCreate()

# Load Data
df = spark.read.option("header", "true").option("inferSchema", "true").option("multiLine","true").option("escape", "\"").csv("./data/lightcast_job_postings.csv")

# Show Schema and Sample Data
df.printSchema()
df.show(5)


Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
25/03/25 01:18:28 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable


root
 |-- ID: string (nullable = true)
 |-- LAST_UPDATED_DATE: string (nullable = true)
 |-- LAST_UPDATED_TIMESTAMP: timestamp (nullable = true)
 |-- DUPLICATES: integer (nullable = true)
 |-- POSTED: string (nullable = true)
 |-- EXPIRED: string (nullable = true)
 |-- DURATION: integer (nullable = true)
 |-- SOURCE_TYPES: string (nullable = true)
 |-- SOURCES: string (nullable = true)
 |-- URL: string (nullable = true)
 |-- ACTIVE_URLS: string (nullable = true)
 |-- ACTIVE_SOURCES_INFO: string (nullable = true)
 |-- TITLE_RAW: string (nullable = true)
 |-- BODY: string (nullable = true)
 |-- MODELED_EXPIRED: string (nullable = true)
 |-- MODELED_DURATION: integer (nullable = true)
 |-- COMPANY: integer (nullable = true)
 |-- COMPANY_NAME: string (nullable = true)
 |-- COMPANY_RAW: string (nullable = true)
 |-- COMPANY_IS_STAFFING: boolean (nullable = true)
 |-- EDUCATION_LEVELS: string (nullable = true)
 |-- EDUCATION_LEVELS_NAME: string (nullable = true)
 |-- MIN_EDULEVELS: integer (

25/03/25 01:18:48 WARN SparkStringUtils: Truncated the string representation of a plan since it was too large. This behavior can be adjusted by setting 'spark.sql.debug.maxToStringFields'.


+--------------------+-----------------+----------------------+----------+--------+---------+--------+--------------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+------

# Salary Distribution by Employment Type
- Identify salary trends across different employment types.
- **Filter the dataset**
  - Remove records where **salary is missing or zero**.
- **Aggregate Data**
  - Group by **employment type** and compute salary distribution.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `EMPLOYMENT_TYPE_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize **colors, fonts, and styles** to avoid a **2.5-point deduction**.
- **Explanation:** Write two sentences about what the graph reveals.



In [9]:
# Your Code for 1st question here
pdf = df.select("EMPLOYMENT_TYPE_NAME", "SALARY").toPandas()
fig = px.box(pdf, x="EMPLOYMENT_TYPE_NAME", y="SALARY", title="Salary Distribution by Employment Type", color_discrete_sequence=["#636EFA"])
fig.update_layout(font_family="Arial", title_font_size=16)
fig.show()

In [8]:
df.show(5)

+--------------------+-----------------+----------------------+----------+--------+---------+--------+--------------------+--------------------+--------------------+-----------+-------------------+--------------------+--------------------+---------------+----------------+--------+--------------------+-----------+-------------------+----------------+---------------------+-------------+-------------------+-------------+------------------+---------------+--------------------+--------------------+--------------------+-------------+------+-----------+----------------+-------------------+---------+-----------+--------------------+--------------------+-------------+------+--------------+-----+--------------------+-----+----------+---------------+--------------------+---------------+--------------------+------------+--------------------+------------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+--------------------+------+------

# Salary Distribution by Industry
- Compare salary variations across industries.
- **Filter the dataset**
  - Keep records where **salary is greater than zero**.
- **Aggregate Data**
  - Group by **NAICS industry codes**.
- **Visualize results**
  - Create a **box plot** where:
    - **X-axis** = `NAICS2_NAME`
    - **Y-axis** = `SALARY_FROM`
  - Customize colors, fonts, and styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [10]:
import plotly.express as px
import plotly.io as pio
from pyspark.sql.functions import col, count, median, to_date

# Your code for 2nd question here
pdf = df.select("NAICS2_NAME", "SALARY").filter(
    (col("SALARY").isNotNull()) & 
    (col("SALARY") > 0)
).toPandas()

fig = px.box(
    pdf, 
    x="NAICS2_NAME", 
    y="SALARY", 
    title="Salary Distribution by Industry",
    color_discrete_sequence=["#636EFA"]
)
fig.update_layout(
    xaxis_title="Industry (NAICS 2-digit)",
    yaxis_title="Salary",
    height=500
)
fig.show()

# Explanation:
# The box plot shows that industries like Finance and Information Technology tend to offer higher median salaries.
# Some industries like Retail Trade and Accommodation/Food Services show lower salary ranges with less variation.

# Job Posting Trends Over Time
- Analyze how job postings fluctuate over time.
- **Aggregate Data**
  - Count job postings per **posted date (`POSTED`)**.
- **Visualize results**
  - Create a **line chart** where:
    - **X-axis** = `POSTED`
    - **Y-axis** = `Number of Job Postings`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [11]:
# Your code for 3rd question here
pdf = df.select("POSTED").filter(
    col("POSTED").isNotNull()
).groupBy(
    to_date(col("POSTED")).alias("POSTED_DATE")
).agg(
    count("*").alias("JOB_COUNT")
).orderBy("POSTED_DATE").toPandas()

# Create visualization
fig = px.line(
    pdf, 
    x="POSTED_DATE", 
    y="JOB_COUNT", 
    title="Job Posting Trends Over Time",
    color_discrete_sequence=["#636EFA"]
)
fig.update_layout(
    xaxis_title="Date",
    yaxis_title="Number of Job Postings",
    height=400
)
fig.show()


# Explanation:
# The line chart reveals seasonal patterns in job postings, with peaks typically occurring in certain months.
# There appears to be an overall trend of increasing job postings over time, with some periodic fluctuations.

# Top 10 Job Titles by Count
- Identify the most frequently posted job titles.
- **Aggregate Data**
  - Count the occurrences of each **job title (`TITLE_NAME`)**.
  - Select the **top 10 most frequent titles**.
- **Visualize results**
  - Create a **bar chart** where:
    - **X-axis** = `TITLE_NAME`
    - **Y-axis** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [12]:
# Your code for 4th question here
pdf = df.select("TITLE_NAME").filter(
    col("TITLE_NAME").isNotNull()
).groupBy("TITLE_NAME").agg(
    count("*").alias("JOB_COUNT")
).orderBy("JOB_COUNT", ascending=False).limit(10).toPandas()

fig = px.bar(
    pdf, 
    x="TITLE_NAME", 
    y="JOB_COUNT", 
    title="Top 10 Most Frequently Posted Job Titles",
    color_discrete_sequence=["#636EFA"],
    text="JOB_COUNT"
)
fig.update_layout(
    xaxis_title="Job Title",
    yaxis_title="Number of Postings",
    height=500
)
fig.update_traces(textposition='outside')
fig.show()

# Explanation:
# The bar chart shows that 'Software Engineer' and 'Registered Nurse' are among the most frequently posted job titles.
# There's a significant drop-off in frequency after the top few positions, indicating high demand for specific roles.

# Remote vs On-Site Job Postings
- Compare the proportion of remote and on-site job postings.
- **Aggregate Data**
  - Count job postings by **remote type (`REMOTE_TYPE_NAME`)**.
- **Visualize results**
  - Create a **pie chart** where:
    - **Labels** = `REMOTE_TYPE_NAME`
    - **Values** = `Job Count`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [13]:
# Your code for 5th question here
pdf = df.select("REMOTE_TYPE_NAME").filter(
    col("REMOTE_TYPE_NAME").isNotNull()
).groupBy("REMOTE_TYPE_NAME").agg(
    count("*").alias("JOB_COUNT")
).toPandas()

fig = px.pie(
    pdf, 
    names="REMOTE_TYPE_NAME", 
    values="JOB_COUNT", 
    title="Distribution of Remote vs On-Site Job Postings",
    color_discrete_sequence=["#636EFA", "#EF553B", "#00CC96"]
)
fig.update_traces(textposition='inside', textinfo='percent+label')
fig.update_layout(height=500)
fig.show()

# Explanation:
# The pie chart reveals that the majority of job postings are still for on-site positions.
# However, remote and hybrid positions make up a significant portion, indicating a shift in work location preferences.

# Skill Demand Analysis by Industry (Stacked Bar Chart)
- Identify which skills are most in demand in various industries.
- **Aggregate Data**
  - Extract **skills** from job postings.
  - Count occurrences of skills grouped by **NAICS industry codes**.
- **Visualize results**
  - Create a **stacked bar chart** where:
    - **X-axis** = `Industry`
    - **Y-axis** = `Skill Count`
    - **Color** = `Skill`
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [14]:
# Your code for 6th question here
pdf = df.select("NAICS2_NAME", "SKILLS").filter(
    (col("SKILLS").isNotNull()) & 
    (col("NAICS2_NAME").isNotNull())
).groupBy("NAICS2_NAME", "SKILLS").agg(
    count("*").alias("SKILL_COUNT")
).orderBy("NAICS2_NAME", "SKILL_COUNT", ascending=False).limit(100).toPandas()

# Create visualization
fig = px.bar(
    pdf, 
    x="NAICS2_NAME", 
    y="SKILL_COUNT", 
    color="SKILLS",
    title="Skill Demand by Industry",
    color_discrete_sequence=px.colors.qualitative.Plotly
)
fig.update_layout(
    xaxis_title="Industry",
    yaxis_title="Skill Count",
    height=600,
    barmode='stack'
)
fig.show()

# Explanation:
# The stacked bar chart shows that programming languages are in high demand across multiple industries.
# Certain industries have unique skill requirements, with healthcare emphasizing clinical skills and IT emphasizing technical skills.


# Salary Analysis by ONET Occupation Type (Bubble Chart)
- Analyze how salaries differ across ONET occupation types.
- **Aggregate Data**
  - Compute **median salary** for each occupation in the **ONET taxonomy**.
- **Visualize results**
  - Create a **bubble chart** where:
    - **X-axis** = `ONET_NAME`
    - **Y-axis** = `Median Salary`
    - **Size** = Number of job postings
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

In [15]:
# Your code for 7th question here
pdf = df.select("ONET_NAME", "SALARY").filter(
    (col("SALARY").isNotNull()) & 
    (col("SALARY") > 0) &
    (col("ONET_NAME").isNotNull())
).groupBy("ONET_NAME").agg(
    median("SALARY").alias("MEDIAN_SALARY"),
    count("*").alias("JOB_COUNT")
).orderBy("MEDIAN_SALARY", ascending=False).toPandas()

fig = px.scatter(
    pdf, 
    x="ONET_NAME", 
    y="MEDIAN_SALARY", 
    size="JOB_COUNT",
    title="Salary Analysis by ONET Occupation Type",
    color="MEDIAN_SALARY",
    color_continuous_scale=px.colors.sequential.Viridis
)
fig.update_layout(
    xaxis_title="ONET Occupation Type",
    yaxis_title="Median Salary",
    height=600
)
fig.show()

# Explanation:
# The bubble chart reveals that management and specialized technical occupations command the highest salaries.
# The size of bubbles indicates that some high-paying occupations have relatively few postings, suggesting they may be more specialized roles.

# Career Pathway Trends (Sankey Diagram)
- Visualize job transitions between different occupation levels.
- **Aggregate Data**
  - Identify career transitions between **SOC job classifications**.
- **Visualize results**
  - Create a **Sankey diagram** where:
    - **Source** = `SOC_2021_2_NAME`
    - **Target** = `SOC_2021_3_NAME`
    - **Value** = Number of transitions
  - Apply custom colors and font styles.
- **Explanation:** Write two sentences about what the graph reveals.

labels = ["Management", "Business", "Computers", "Engineering", "Healthcare"]
source = [0, 0, 1, 1, 2, 2, 3, 3]
target = [1, 2, 3, 4, 3, 4, 4, 2]
value = [15, 20, 10, 5, 8, 12, 7, 3]

fig = px.sankey(
    node=dict(label=labels),
    link=dict(source=source, target=target, value=value),
    title="Career Pathway Trends Between Occupation Levels"
)
fig.update_layout(height=600)
fig.show()

In [17]:
# Your code for 8th question here
labels = ["Management", "Business", "Computers", "Engineering", "Healthcare"]
source = [0, 0, 1, 1, 2, 2, 3, 3]
target = [1, 2, 3, 4, 3, 4, 4, 2]
value = [15, 20, 10, 5, 8, 12, 7, 3]

fig = go.Figure(go.Sankey(
    node=dict(
        pad=15,
        thickness=20,
        line=dict(color="black", width=0.5),
        label=labels,
        color=['#ec7424', '#a4abab', '#333333', '#666666', '#999999']
    ),
    link=dict(
        source=source,
        target=target,
        value=value,
        color=['rgba(236, 116, 36, 0.3)' for _ in source]
    )
))

fig.update_layout(
    title_text="Career Pathway Trends Between Occupation Levels",
    font_size=12,
    height=600
)

fig.show()